# Classical Shadow

In [10]:
import data_acquisition_shadow
import prediction_shadow
from prediction_shadow import estimate_exp

from qutip import *
# from quantum_state_utils import *
from qutip.measurement import measure, measurement_statistics, measure_observable
# from Code.quantum_state_utils import generate_rand_product_density
import sys, random, math
import numpy as np

import matplotlib.pyplot as plt
import matplotlib as mpl
mpl.rcParams['figure.dpi'] = 400
import matplotlib.pyplot as plt

SMALL_SIZE = 10
MEDIUM_SIZE = 11  #default 10
LARGE_SIZE = 13
plt.rc('font', size=MEDIUM_SIZE)  # controls default text sizes
plt.rc('axes', titlesize=LARGE_SIZE)  # fontsize of the axes title
plt.rc('axes', labelsize=LARGE_SIZE)  # fontsize of the x and y labels
plt.rc('xtick', labelsize=MEDIUM_SIZE)  # fontsize of the tick labels
plt.rc('ytick', labelsize=MEDIUM_SIZE)  # fontsize of the tick labels

pauli_dict = {'I': identity(2), 'X': sigmax(), 'Y': sigmay(), 'Z': sigmaz()}

def estimate_exp(full_measurement, one_observable):
    sum_product, cnt_match = 0, 0

    # print(one_observable)
    for single_measurement in full_measurement:
        not_match = 0
        product = 1

        for pauli_XYZ, position in one_observable:
            if pauli_XYZ != single_measurement[position][0]:
                not_match = 1
                break
            product *= single_measurement[position][1]
            # print(product)
        if not_match == 1: continue

        sum_product += product
        cnt_match += 1

    return sum_product, cnt_match

def randomized_classical_shadow(num_total_measurements, system_size):
    #
    # Implementation of the randomized classical shadow
    #
    #    num_total_measurements: int for the total number of measurement rounds
    #    system_size: int for how many qubits in the quantum system
    #
    measurement_procedure = []
    for t in range(num_total_measurements):
        single_round_measurement = [random.choice(["X", "Y", "Z"]) for i in range(system_size)]
        measurement_procedure.append(single_round_measurement)
    return measurement_procedure

# ghz = ket2dm(ghz_state(3))
# pob = tensor(sigmax(),qeye(2),qeye(2))
# pob = tensor(sigmax(),sigmax(),sigmaz())



In [ ]:
## derandomized



In [11]:
# measurement_file = 'measurement_3.txt'
# observables_file = 'observables_3.txt'
measurement_file = 'measurement_10.txt'
observables_file = 'observables_10.txt'

with open(measurement_file) as f:
    measurements = f.readlines()
system_size = int(measurements[0])
print('measurements:',measurements[1])

full_measurement = []
for line in measurements[1:]:
    single_meaurement = []
    for pauli_XYZ, outcome in zip(line.split(" ")[0::2], line.split(" ")[1::2]):
        single_meaurement.append((pauli_XYZ, int(outcome)))
    full_measurement.append(single_meaurement)
print('full_measurement:',full_measurement[1])
print('size of shadow:', len(full_measurement))

# with open(sys.argv[3]) as f:
with open(observables_file) as f:
    content = f.readlines()
assert(system_size == int(content[0]))
print('observables:',content)

n_qubit = int(measurements[0])
five_singlet = tensor([singlet_state() for i in range(5)])
for line in content[1:]:
    one_observable = []
    local_observable_string = ['I' for i in range(n_qubit)]
    for pauli_XYZ, position in zip(line.split(" ")[1::2], line.split(" ")[2::2]):
        one_observable.append((pauli_XYZ, int(position)))
        local_observable_string[int(position)]=pauli_XYZ
    local_observable = tensor([ pauli_dict[operator] for operator in local_observable_string])
    # print(one_observable)
    
    # print(one_observable)
    sum_product, cnt_match = estimate_exp(full_measurement, one_observable)
    print(f'local observable: {one_observable}, shadow estimation: {sum_product / cnt_match:.3f}, expectation values: {expect(oper=local_observable,state=five_singlet)}')

measurements: Z 1 Z -1 Y 1 Z 1 Z 1 Z -1 Y 1 Y -1 Z -1 X 1 

full_measurement: [('Y', -1), ('X', -1), ('Y', 1), ('Y', -1), ('Y', -1), ('Y', 1), ('Y', 1), ('Z', -1), ('Y', 1), ('X', -1)]
size of shadow: 20000
observables: ['10\n', '2 X 0 Y 1\n', '2 X 1 Y 2\n', '2 X 2 Y 3\n', '2 X 3 Y 4\n', '2 X 4 Y 5\n', '2 X 5 Y 6\n', '2 X 6 Y 7\n', '2 X 7 Y 8\n', '2 X 8 Y 9\n', '2 X 0 Y 4\n', '2 X 1 Y 5\n', '2 X 2 Y 6\n', '2 X 3 Y 7\n', '2 X 4 Y 8\n', '4 X 0 X 1 X 2 X 3\n', '4 X 4 X 5 X 6 X 7\n']
local observable: [('X', 0), ('Y', 1)], shadow estimation: 0.049, expectation values: 0.0
local observable: [('X', 1), ('Y', 2)], shadow estimation: 0.007, expectation values: 0.0
local observable: [('X', 2), ('Y', 3)], shadow estimation: 0.015, expectation values: 0.0
local observable: [('X', 3), ('Y', 4)], shadow estimation: -0.005, expectation values: 0.0
local observable: [('X', 4), ('Y', 5)], shadow estimation: 0.018, expectation values: 0.0
local observable: [('X', 5), ('Y', 6)], shadow estimation: -0.02

In [28]:
random_measurements = randomized_classical_shadow(20000, n_qubit)
# print(random_measurements)

def single_copy_measurement(state,pob):
    measure_observable(state, pob)
    eigenvalues, eigenstates, probabilities = measurement_statistics(state, pob)

    print('probabilities of two outcomes:',(1-np.inner(eigenvalues, probabilities))/2,(1+np.inner(eigenvalues, probabilities))/2)
    return 1 if random.random() < (1+np.inner(eigenvalues, probabilities))/2 else -1

state_0, state_1 = basis(2, 0), basis(2, 1)
Z0, Z1 = ket2dm(state_0), ket2dm(state_1)

n_qubit = 10
five_singlet = tensor([ket2dm(singlet_state()) for i in range(5)])

def rotate_measure(state, random_unitary):
    projector_Z0 = [Z0] + [identity(2) for i in range(n_qubit - 1)]
    # projector_Z0.append(projector_Z0.pop(0))
    projector_Z1 = [Z1] + [identity(2) for i in range(n_qubit - 1)]
    # print(len(projector_Z0))
    print('============ rotate measure ==============')
    # print(pob)
    print(random_unitary)
    op = tensor([pauli_dict[i] for i in random_unitary])
    # print(op.dims)
    # print(state.dims)
    state_rotated = op.dag() * state * op
    outcomes = []
    for i in range(n_qubit):
        projector = [tensor(projector_Z0), tensor(projector_Z1)]
        collapsed_states, probabilities = measurement_statistics(
            state_rotated, projector)
        # print(collapsed_states)
        # print(
        #     f'{i+1}-th qubit two-outcome probabilities: Prob(|0>,1)={probabilities[0]:.5f}, Prob(|1>,-1)={probabilities[1]:.5f}'
        # )
        outcomes.append((random_unitary[i],
                         1 if random.random() < probabilities[0] else -1))

        # print(projector_Z0)
        projector_Z0.insert(0, projector_Z0.pop(-1))
        projector_Z1.insert(0, projector_Z1.pop(-1))
        # projector_Z0.append(projector_Z0.pop(0))
        # projector_Z1.append(projector_Z1.pop(0))

    print(outcomes)
    return outcomes


full_measurement = []
for index, random_measurement in enumerate(random_measurements):
    print(index)
    pob = tensor([pauli_dict[i] for i in random_measurement])
    # print(random_measurement)
    # print('============ single-copy measure ==============')
    # for index, ob in enumerate(random_measurement):
    #     nob = [qeye(2) for i in range(n_qubit - 1)]
    #     nob.insert(index, pauli_dict[ob])
    #     # result_str += ob+' '
    #     # print(nob)
    #     outcome = single_copy_measurement(five_singlet, tensor(nob))
    #     print(random_measurement[index],outcome)
    full_measurement.append(rotate_measure(five_singlet, random_measurement))



0
============ rotate measure ==============
['Y', 'X', 'X', 'X', 'Z', 'X', 'Y', 'X', 'Y', 'Z']
[('Y', -1), ('X', 1), ('X', -1), ('X', 1), ('Z', -1), ('X', 1), ('Y', -1), ('X', -1), ('Y', 1), ('Z', -1)]
1
============ rotate measure ==============
['X', 'Y', 'X', 'Z', 'Z', 'X', 'X', 'X', 'Y', 'X']
[('X', 1), ('Y', -1), ('X', -1), ('Z', -1), ('Z', -1), ('X', -1), ('X', 1), ('X', 1), ('Y', 1), ('X', -1)]
2
============ rotate measure ==============
['Z', 'X', 'Y', 'Y', 'X', 'X', 'Z', 'Y', 'Z', 'Y']
[('Z', -1), ('X', 1), ('Y', -1), ('Y', 1), ('X', -1), ('X', -1), ('Z', 1), ('Y', 1), ('Z', 1), ('Y', 1)]
3
============ rotate measure ==============
['X', 'Z', 'Y', 'Y', 'Y', 'Y', 'Z', 'X', 'Z', 'Y']
[('X', -1), ('Z', 1), ('Y', 1), ('Y', 1), ('Y', -1), ('Y', -1), ('Z', -1), ('X', 1), ('Z', -1), ('Y', 1)]
4
============ rotate measure ==============
['Z', 'Z', 'Y', 'X', 'Z', 'Z', 'X', 'Z', 'Y', 'Y']
[('Z', 1), ('Z', -1), ('Y', 1), ('X', 1), ('Z', 1), ('Z', 1), ('X', -1), ('Z', 1), ('Y', 1), ('

In [33]:
print(full_measurement[1])

with open(observables_file) as f:
    content = f.readlines()
assert (system_size == int(content[0]))
print('observables:', content)

for line in content[1:]:
    one_observable = []
    local_observable_string = ['I' for i in range(n_qubit)]
    for pauli_XYZ, position in zip(
            line.split(" ")[1::2],
            line.split(" ")[2::2]):
        one_observable.append((pauli_XYZ, int(position)))
        local_observable_string[int(position)] = pauli_XYZ
    local_observable = tensor(
        [pauli_dict[operator] for operator in local_observable_string])
    # print(one_observable)

    # print(one_observable)
    sum_product, cnt_match = estimate_exp(full_measurement, one_observable)
    print(
        f'local observable: {one_observable}, shadow estimation: {sum_product / cnt_match:.3f}, expectation values: {expect(oper=local_observable,state=five_singlet)}'
    )


[('X', 1), ('Y', -1), ('X', -1), ('Z', -1), ('Z', -1), ('X', -1), ('X', 1), ('X', 1), ('Y', 1), ('X', -1)]
observables: ['10\n', '2 X 0 Y 1\n', '2 X 1 Y 2\n', '2 X 2 Y 3\n', '2 X 3 Y 4\n', '2 X 4 Y 5\n', '2 X 5 Y 6\n', '2 X 6 Y 7\n', '2 X 7 Y 8\n', '2 X 8 Y 9\n', '2 X 0 Y 4\n', '2 X 1 Y 5\n', '2 X 2 Y 6\n', '2 X 3 Y 7\n', '2 X 4 Y 8\n', '4 X 0 X 1 X 2 X 3\n', '4 X 4 X 5 X 6 X 7\n']
local observable: [('X', 0), ('Y', 1)], shadow estimation: -0.011, expectation values: 0.0
local observable: [('X', 1), ('Y', 2)], shadow estimation: -0.010, expectation values: 0.0
local observable: [('X', 2), ('Y', 3)], shadow estimation: -0.034, expectation values: 0.0
local observable: [('X', 3), ('Y', 4)], shadow estimation: 0.007, expectation values: 0.0
local observable: [('X', 4), ('Y', 5)], shadow estimation: 0.000, expectation values: 0.0
local observable: [('X', 5), ('Y', 6)], shadow estimation: 0.005, expectation values: 0.0
local observable: [('X', 6), ('Y', 7)], shadow estimation: -0.033, expec

In [2]:
# python data_acquisition_shadow.py -r 30 5
# python generate_observables.py
# python prediction_shadow.py -o measurement.txt observables.txt

## Versions of software package/module 

In [13]:
# about()
# conda list
# from qutip.ipynbtools import version_table
# version_table()
# qutip.cite()

print('numpy version:', np.__version__)
print('matplotlib version', mpl.__version__)

import sklearn
print('Scikit-learn version:', sklearn.__version__)
print('QuTiP version:', qutip.__version__)

numpy version: 1.21.5
matplotlib version 3.5.1
Scikit-learn version: 1.1.2
QuTiP version: 4.7.0
